In [0]:

pip install yfinance

  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 949.2/949.2 kB 20.1 MB/s eta 0:00:00
  Installing build dependencies: started
  Installing build dependencies: finished with status 'done'
  Getting requirements to build wheel: started
  Getting requirements to build wheel: finished with status 'done'
  Preparing metadata (pyproject.toml): started
  Preparing metadata (pyproject.toml): finished with status 'done'
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.3/8.3 MB 65.7 MB/s eta 0:00:00
  Created wheel for multitasking: filename=multitasking-0.0.12-py3-none-any.whl size=15548 sha256=9b8c04673ef6d8d1afef5cc4e16d19efcff14a4ba3f41f346d7f597650cb09c4
  Stored in directory: /root/.cache/pip/wheels/cc/bd/6f/664d62c99327abeef7d86489e6631cbf45b56fbf7ef1d6ef00
  Created wheel for peewee: filename=peewee-3.18.2-cp312-cp312-linux_x86_64.whl size=942235 sha256=d44f30268bc1ea6e31335ddc7a527d9435cf7f83f

In [0]:

dbutils.library.restartPython()

In [0]:
storage_account_name = "datalakedemo64380"
storage_account_key = "tZyDnI6oe5hOo1XuxKhJ0cKA14yzCNRZxrrj0bKpJow1nsbuhdXlxg0ZTRKnbb7ztv2usY1QhICC+AStYbNTaA=="
raw_container = "raw"
curated_container = "curated"

In [0]:
spark.conf.set(
  f"fs.azure.account.key.{storage_account_name}.dfs.core.windows.net",
  storage_account_key
)
print("Azure Storage key is successful loaded to Spark。")

Azure Storage key is successful loaded to Spark。


In [0]:
test_df = spark.createDataFrame([(1,"ok"),(2,"connected")],["id","msg"])
test_path = f"abfss://raw@{storage_account_name}.dfs.core.windows.net/test_parquet"
test_df.write.mode("overwrite").parquet(test_path)
display(spark.read.parquet(test_path))

id msg 2 connected 1 ok

In [0]:
import os
import time
from datetime import datetime
import pandas as pd
import yfinance as yf
from azure.storage.blob import BlobServiceClient, BlobClient, ContainerClient

# === CONFIG ===
account_name = storage_account_name
account_key = storage_account_key
container_name = "raw"
prefix = "stocks"
tickers = ["AAPL", "MSFT", "AMZN", "GOOGL", "META", "NVDA", "TSLA", "NFLX", "AVGO", "AMD"]
start_date = "2015-01-01"

# === Initialize Azure Blob Service ===
connection_str = f"DefaultEndpointsProtocol=https;AccountName={account_name};AccountKey={account_key};EndpointSuffix=core.windows.net"
blob_service = BlobServiceClient.from_connection_string(connection_str)
container_client = blob_service.get_container_client(container_name)

print("Connected to Azure Blob Storage (ADLS Gen2)")


Connected to Azure Blob Storage (ADLS Gen2)


In [0]:
def blob_exists(container_client, blob_path):
    """Check if blob exists in container"""
    try:
        blob_client = container_client.get_blob_client(blob_path)
        return blob_client.exists()
    except Exception as e:
        print(f"Check failed: {e}")
        return False


def upload_to_blob(local_file, blob_path):
    """Upload local file to ADLS"""
    try:
        blob_client = container_client.get_blob_client(blob_path)
        with open(local_file, "rb") as data:
            blob_client.upload_blob(data, overwrite=True)
        print(f"✅ Uploaded to abfss://{container_name}@{account_name}.dfs.core.windows.net/{blob_path}")
    except Exception as e:
        print(f"❌ Upload failed for {blob_path}: {e}")


In [0]:
for t in tickers:
    print(f"\n⬇️ Downloading {t} ...")

    # --- Download from Yahoo Finance ---
    try:
        df = yf.download(t, start=start_date, interval="1d", auto_adjust=True, progress=False)
        if df.empty:
            print(f"{t}: No data, skipped.")
            continue
    except Exception as e:
        print(f"Error downloading {t}: {e}")
        continue

    df = df.reset_index()

    # --- Normalize columns ---
    if isinstance(df.columns, pd.MultiIndex):
        df.columns = ["_".join([str(c) for c in col if c]).strip().lower().replace(" ", "_") for col in df.columns]
    else:
        df.columns = [str(c).lower().replace(" ", "_") for c in df.columns]

    df.columns = [c.replace(f"_{t.lower()}", "") for c in df.columns]

    # --- Ensure all required columns ---
    for col_name in ["date", "open", "high", "low", "close", "adj_close", "volume"]:
        if col_name not in df.columns:
            df[col_name] = None

    # --- Add metadata ---
    df["ticker"] = t
    df["source"] = "yfinance"
    df["interval"] = "1d"
    df["ingestion_date"] = datetime.utcnow().strftime("%Y-%m-%d %H:%M:%S")
    df["is_valid"] = True

    df = df[
        ["date", "open", "high", "low", "close", "adj_close", "volume", "ticker",
         "source", "interval", "ingestion_date", "is_valid"]
    ]

    # --- Save locally ---
    local_file = f"/tmp/stocks_{t}.csv"
    df.to_csv(local_file, index=False)

    # --- Upload to ADLS raw ---
    blob_path = f"{prefix}/ticker={t}/stocks_{t}.csv"
    if blob_exists(container_client, blob_path):
        print(f"{t} already exists, overwriting ...")
    upload_to_blob(local_file, blob_path)

    os.remove(local_file)
    time.sleep(1)



⬇️ Downloading AAPL ...


/root/.ipykernel/1483/command-5779569815290270-1166275481:33: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  df["ingestion_date"] = datetime.utcnow().strftime("%Y-%m-%d %H:%M:%S")


✅ Uploaded to abfss://raw@datalakedemo64380.dfs.core.windows.net/stocks/ticker=AAPL/stocks_AAPL.csv

⬇️ Downloading MSFT ...


/root/.ipykernel/1483/command-5779569815290270-1166275481:33: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  df["ingestion_date"] = datetime.utcnow().strftime("%Y-%m-%d %H:%M:%S")


✅ Uploaded to abfss://raw@datalakedemo64380.dfs.core.windows.net/stocks/ticker=MSFT/stocks_MSFT.csv

⬇️ Downloading AMZN ...


...

✅ Uploaded to abfss://raw@datalakedemo64380.dfs.core.windows.net/stocks/ticker=NFLX/stocks_NFLX.csv

⬇️ Downloading AVGO ...


/root/.ipykernel/1483/command-5779569815290270-1166275481:33: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  df["ingestion_date"] = datetime.utcnow().strftime("%Y-%m-%d %H:%M:%S")


✅ Uploaded to abfss://raw@datalakedemo64380.dfs.core.windows.net/stocks/ticker=AVGO/stocks_AVGO.csv

⬇️ Downloading AMD ...


/root/.ipykernel/1483/command-5779569815290270-1166275481:33: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  df["ingestion_date"] = datetime.utcnow().strftime("%Y-%m-%d %H:%M:%S")


✅ Uploaded to abfss://raw@datalakedemo64380.dfs.core.windows.net/stocks/ticker=AMD/stocks_AMD.csv


In [0]:
from pyspark.sql.functions import col, avg, round
from pyspark.sql import Window

# === Read raw CSVs ===
raw_path = f"abfss://raw@{storage_account_name}.dfs.core.windows.net/stocks/"
df = spark.read.option("header", True).csv(raw_path, inferSchema=True)

# === Calculate SMA_5 ===
windowSpec = Window.partitionBy("ticker").orderBy("date").rowsBetween(-4, 0)
df_sma = df.withColumn("SMA_5", round(avg(col("close")).over(windowSpec), 2))

# === Write to curated layer ===
curated_path = f"abfss://curated@{storage_account_name}.dfs.core.windows.net/yfinance_curated"
df_sma.write.mode("overwrite").parquet(curated_path)

print(f"✅ Curated data saved to {curated_path}")


✅ Curated data saved to abfss://curated@datalakedemo64380.dfs.core.windows.net/yfinance_curated


In [0]:
display(spark.read.parquet(f"abfss://curated@{storage_account_name}.dfs.core.windows.net/yfinance_curated"))

date open high low close adj_close volume ticker source interval ingestion_date is_valid SMA_5 2015-01-02 24.718174386973395 24.729270393437197 23.821671579713147 24.26104736328125 null 212818400 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 24.26 2015-01-05 24.030267283850048 24.110153799834524 23.391176848987335 23.577577590942383 null 257142000 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 23.92 2015-01-06 23.64192558989593 23.83942229690088 23.218083238966898 23.579792022705078 null 263188400 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 23.81 2015-01-07 23.78838352536704 24.01029009442088 23.677430240840117 23.910432815551758 null 160423600 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 23.83 2015-01-08 24.23885761526062 24.886824452930725 24.121245700213183 24.82912826538086 null 237458000 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 24.03 2015-01-09 25.002212305020397 25.130918519212265 24.456322357565924 24.855754852294922 null 214798000 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 24.15 2015-01-12 24.986684395122083 24.993341322659273 24.143440277820233 24.243297576904297 null 198603200 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 24.28 2015-01-13 24.72705053894741 25.03106316625113 24.16784669635183 24.45854377746582 null 268367600 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 24.46 2015-01-14 24.196697407787628 24.518461321069434 24.076867632996397 24.365346908569336 null 195826400 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 24.55 2015-01-15 24.409726485276778 24.4230403397773 23.668559239188266 23.704063415527344 null 240056000 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 24.33 2015-01-16 23.75065951213766 23.87270880076629 23.34457008962357 23.51987648010254 null 314053200 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 24.06 2015-01-20 23.93040774732097 24.18116329739943 23.63305370582818 24.125686645507812 null 199599600 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 24.03 2015-01-21 24.176724446024636 24.644947527863252 24.02582788373049 24.30986976623535 null 194303600 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 24.0 2015-01-22 24.467415221160643 24.9578284643181 24.347585488129347 24.94229507446289 null 215185600 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 24.12 2015-01-23 24.920106437303215 25.24187026011724 24.749237444378423 25.071002960205078 null 185859200 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 24.39 2015-01-26 25.23965535290147 25.377238049714297 25.03106430723337 25.09763526916504 null 222460000 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 24.71 2015-01-27 24.946736811155496 24.960052356934085 24.1944736556585 24.218883514404297 null 382274800 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 24.73 2015-01-28 26.10286827631415 26.211603710653883 25.588045120239258 25.588045120239258 null 585908400 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 24.98 2015-01-29 25.812175619330834 26.449048170199948 25.6435261294502 26.384695053100586 null 337745600 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 25.27 2015-01-30 26.27373889027836 26.62878907264439 25.929783020884912 25.99857521057129 null 334982000 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 25.46 2015-02-02 26.19607686641939 26.44461119442779 25.758920559173443 26.32478141784668 null 250956400 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 25.7 2015-02-03 26.295923963069487 26.42684800391051 26.098427285623295 26.32921028137207 null 207662800 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 26.13 2015-02-04 26.295932269467976 26.74196501238614 26.25376947343209 26.531152725219727 null 280598800 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 26.31 2015-02-05 26.738337501467665 26.78512329175272 26.56679583596891 26.720516204833984 null 168984800 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 26.38 2015-02-06 26.73833824448596 26.789578935429713 26.38857000537499 26.495506286621094 null 174826400 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 26.48 2015-02-09 26.41084246075367 26.698230133283793 26.384107972746513 26.671497344970703 null 155559200 AAPL yfinance 1.0 2025-10-22T20:05:45Z true 26.55 2015